In [2]:
import re
import pandas as pd
import matplotlib.pyplot as plt
import matplotlib as mpl
from sklearn import metrics
from sklearn.model_selection import train_test_split
import catboost as cb
import os
from IPython import embed
from datetime import date
from sklearn.preprocessing import MinMaxScaler
import numpy as np
from statsmodels.tsa.statespace.sarimax import SARIMAX

In [3]:
#Qt de unidades de saude, precipitação média no ultimo mes, temperatura média no ultimo mês,
#umidade do ar média no último mês, soma de casos em bairros vizinhas (por bairro), casos de dengue 1 mes atras,
#casos de dengue 2 meses atras, casos de dengue 3 meses atras, densidade demografica (do bairro), casos de zika ultimo mes,
#casos de chikungunya ultimo mes, ? , liraa (índice levantado a partir de indicadores de infestação de Aedes Aegypti)
selected_columns = ['qtd_cnes', 'precipitacao (mm)-1', 'temperatura (°C)-1',
       'umidade ar (%)-1', 'sum_vizinhos_t-1',
       't-1', 't-2', 't-3', 'densidade_demografica',
       'zika-1', 'chikungunya-1', 'critical_neighbor', 'liraa']

base_path = os.getcwd()
dengue_columns = ['t-1', 't-2', 't-3', 'sum_vizinhos_t-1', 'dengue_diagnosis'] #casos ultimo mes, penultimo mes, antepenultimo mes, soma de casos vizinhos ultimo mes, e casos no mes atual
categorical_columns = []
columns_filtered_categorical = []
neighbor_columns=['sum_vizinhos_t-1']
log_flag = False
target = 'dengue_diagnosis' #casos de dengue
year_begin = 2016
year_end = 2020
list_year = list(range(year_begin, year_end+1))
model = "catboost"
standart = False
months = list(range(1, 13))
months_ahead_predict = 3
file_name = f"{year_begin}_{year_end}_{months_ahead_predict}_months"
fontsize_title = 15
fontsize_label = 14
dpi = 180

pd.options.mode.chained_assignment = None #Warning


In [4]:
def base_prepare(df_dengue_origem, ano_teste=2019,
                        mes_inicio_teste=1,
                        meses_previsao=6):

    df_dengue_origem['data'] = df_dengue_origem[['ano', 'mes']].apply(lambda x: date(x[0], x[1], 1), axis=1)

    list_data_teste = list()
    for m in list(range(mes_inicio_teste, mes_inicio_teste+meses_previsao)):
        if m < 13:
            list_data_teste.append(date(ano_teste, m, 1))
        else:
            list_data_teste.append(date(ano_teste+1, m-12, 1))

    # Filter dates which is in test data list
    df_teste = df_dengue_origem[df_dengue_origem['data'].isin(list_data_teste)]

    # Filter dates which is not in test data list
    df_treino = df_dengue_origem[~df_dengue_origem['data'].isin(list_data_teste)]

    df_treino.drop(columns=['data'], inplace=True)
    df_teste.drop(columns=['data'], inplace=True)

    return df_treino, df_teste

In [5]:
def prepare_base_train(df_treino, columns_filtered, columns_filtered_categorical,
                            categorical_columns, target_variable='dengue_diagnosis'):

    X_train = df_treino[columns_filtered]
    y_train = df_treino[target_variable]

    X_train = pd.get_dummies(X_train, columns=categorical_columns)

    # Para o caso de haver variáveis categoricas que serão selecionadas
    if not columns_filtered_categorical == []:

        # Tratativa especial para o caso de mês
        if 'mes' in categorical_columns:

            # Irá buscar somente os meses que estão na base de treino, pode ir de 1 a 12
            mes_list = ["mes_{}".format(i) for i in list(df_treino["mes"].unique())]
            mes_list = [m for m in mes_list if m in columns_filtered_categorical]
            categorical_list = [a for a in categorical_columns if not re.match(".*mes.*", a)]

            # Se na lista de variáveis categoricas não tivessem somente o mês
            if len(categorical_list) > 0:
                columns_filtered_categorical_new = categorical_list + mes_list
            else:
                columns_filtered_categorical_new = mes_list

        new_columns_features = [a for a in columns_filtered if a not in categorical_columns]
        X_train = X_train[new_columns_features + columns_filtered_categorical_new]

        meses_ausentes = [m for m in columns_filtered_categorical if re.match(".*mes.*", m) and not m in mes_list]
        if len(meses_ausentes) > 0:
            for m in meses_ausentes:
                X_train[m] = [0] * X_train.shape[0]


    columns, index_time_cols = get_indices_columns_time(X_train.columns)
    X_train = X_train[columns]

    return X_train, y_train



In [6]:
def get_indices_columns_time2(columns):

    columns_time_um = list()
    columns_time_tres = list()
    columns_time_seis = list()
    columns_others = list()

    for c in columns:
        if re.match(".*\(t-1\).*", c):
            columns_time_um.append(c)
        elif re.match(".*\(t-3\).*", c):
            columns_time_tres.append(c)
        elif re.match(".*\(t-6\).*", c):
            columns_time_seis.append(c)
        else:
            columns_others.append(c)

    columns_sequence = columns_others + columns_time_um + columns_time_tres + columns_time_seis

    index_time_cols_um = (len(columns_others), len(columns_others) + len(columns_time_um) - 1)
    index_time_cols_tres = (index_time_cols_um[1]+1,  index_time_cols_um[1] + len(columns_time_tres))
    index_time_cols_seis = (index_time_cols_tres[1] + 1, index_time_cols_tres[1] + len(columns_time_seis))

    return columns_sequence, index_time_cols_um, index_time_cols_tres, index_time_cols_seis


In [7]:
def get_indices_columns_time(columns):
    columns_time = list()
    columns_others = list()

    for c in columns:
        if re.match("t-.", c):
            columns_time.append(c)
        else:
            columns_others.append(c)

    if len(columns_time) > 0:

        index_time_cols = (len(columns_others),
                           len(columns_others) + len(columns_time) - 1)

        columns_others = columns_others + columns_time

        return columns_others, index_time_cols

    else:
        return columns_others, list()

In [8]:
def identify_critical_cases_in_data_train_and_test(df_teste, df_treino, target):

    df_pivot = df_treino.pivot_table(index=['nome_bairro'],
                                          values=[target], aggfunc='sum').reset_index()

    scaler = MinMaxScaler(feature_range = (0,1))

    df_pivot['critical_neighbor'] = scaler.fit_transform(np.array(df_pivot[target]).reshape(-1, 1))
    df_pivot['critical_neighbor'] = df_pivot['critical_neighbor'].apply(lambda x: round(x, 2))

    df_teste = pd.merge(df_teste, df_pivot[['nome_bairro', 'critical_neighbor']],
                        on='nome_bairro', how='left')

    df_treino = pd.merge(df_treino, df_pivot[['nome_bairro', 'critical_neighbor']],
                        on='nome_bairro', how='left')

    return df_teste, df_treino



In [9]:
def run_main_first_step_1(target, ano_teste, dengue_columns, columns_filtered, categorical_columns,
                             columns_filtered_categorical, mes_inicio_teste=1, sample=False, n=0,
                             meses_previsao=6, log=False, quartil=False, classification=False):
    '''
    Step 1 of main process: prepare train and test bases
    '''
    if target == "taxa_dengue":
        df_dengue_origem = pd.read_csv(base_path + "/data/dengue_input_from_source_taxa_v5.csv")
    else:
        df_dengue_origem = pd.read_csv(base_path + "/data/dengue_input_from_source_v10.csv")

    if not classification == False:
        # Apply shift to predict months ahead
        df_shift = pd.DataFrame(columns=list(df_dengue_origem.columns))
        for n in list(df_dengue_origem['nome_bairro'].unique()):
            df = df_dengue_origem[df_dengue_origem['nome_bairro'] == n]
            df['dengue_diagnosis'] = df['dengue_diagnosis'].shift(classification+1)
            df_shift = df_shift.append(df)

        df_dengue_origem = df_shift.dropna()

    df_dengue_origem.drop(columns=['Unnamed: 0'], inplace=True)
    df_dengue_origem = df_dengue_origem[df_dengue_origem['ano'] > 2014]

    if log:
        for c in list(df_dengue_origem.columns):
            if c in dengue_columns:
                df_dengue_origem[c] = df_dengue_origem[c].replace(0, 1)
                df_dengue_origem[c] = np.log10(df_dengue_origem[c])

    df_treino, df_teste = base_prepare(df_dengue_origem, ano_teste=ano_teste,
                                              mes_inicio_teste=mes_inicio_teste, meses_previsao=meses_previsao)

    if quartil:
        df_teste, df_treino = identify_critical_cases_in_data_train_and_test(df_teste, df_treino, target)

    x_train, y_train = prepare_base_train(df_treino, columns_filtered, columns_filtered_categorical,
                            categorical_columns, target_variable=target)

    if sample:
        x_train_sample, x_test_sample, y_train_sample, y_test_sample = train_test_split(x_train,
                                                                                        y_train,
                                                                                        test_size=0.1,
                                                                                        random_state=n)
    else:
        x_train_sample = x_train.copy()
        y_train_sample = y_train.copy()

    return df_treino, df_teste, x_train_sample, y_train_sample



In [10]:
def run_main_first_step_2(df_test, x_train, y_train, selected_columns, categorical_columns,
           columns_filtered_categorical, neighbor_columns, target, model, standart=False):
    '''
    Step 2 of main process: training model and predicting values
    '''

    if model in ["randomforest", "extratrees", "xgboost", "lightGBM"]:
        # regressor, r2 = globals()["run_{}".format(model)](X_train, y_train, grid_search=False)
        regressor, r2 = run_lightGBM(x_train, y_train, grid_search=False, standart=standart)
        scaler = False
    elif model in ['catboost']:
        regressor, r2 = run_catboost(x_train, y_train, grid_search=False, standart=standart)
        scaler = False
    elif model in ["polynomial_regression"]:
        regressor, scaler, r2 = globals()["run_{}".format(model)](x_train, y_train, grid_search=False)
    else:
        regressor, scaler, r2 = globals()["run_{}".format(model)](x_train, y_train, grid_search=False)
        scaler = False

    train_columns = list(x_train.columns).copy()
    df_output_model = apply_future_prediction_update_neighbors_v2(regressor, df_test,
                                                               selected_columns, columns_filtered_categorical,
                                                               train_columns, categorical_columns,
                                                               neighbor_columns, target=target,
                                                               scaler=scaler)

    df_test = pd.merge(df_test, df_output_model[["chave", target+'_previsto']], on="chave", how="left")

    return df_test, df_output_model, regressor


In [11]:
def prepare_base_test(df_previsao, columns_filtered, columns_filtered_categorical,
                            categorical_columns, train_columns, scaler):

    # O método recebe a base de teste com todas as colunas da base original
    # df_previsao_X é o df que será inserido no modelo para previsão
    df_previsao_X = df_previsao[columns_filtered]

    # Se existem variáveis categoricas então transforma em binário
    if not categorical_columns == []:
        df_previsao_X = pd.get_dummies(df_previsao_X, columns=categorical_columns)

    # para as variáveis categóricas filtra as variáveis e valores previamente secionados
    mes_list = ["mes_{}".format(i) for i in list(df_previsao["mes"].unique())]

    if not columns_filtered_categorical == []:

        # para o caso de análise de r2 no tempo
        if 'mes' in categorical_columns:
            mes_list = [m for m in mes_list if m in columns_filtered_categorical]

            categorical_list = [a for a in categorical_columns if not re.match(".*mes.*", a)]

            # Se houver mais variáveis categóricas além de mes
            if len(categorical_list) > 0:
                columns_filtered_categorical_new = categorical_list + mes_list
            else:
                columns_filtered_categorical_new = mes_list

        new_columns_features = [a for a in columns_filtered if a not in categorical_columns]
        df_previsao_X = df_previsao_X[new_columns_features + columns_filtered_categorical_new]

    # Caso o modelo foi treinado com meses que estão além dos meses na base de teste
    meses_ausentes = [m for m in train_columns if re.match(".*mes.*", m) and not m in mes_list]
    if len(meses_ausentes) > 0:
        for m in meses_ausentes:
            df_previsao_X[m] = [0] * df_previsao_X.shape[0]

    # Se o regressor exige valores normalizados
    if scaler:
        df_previsao_X = pd.DataFrame(scaler.transform(df_previsao_X),
                                     columns=df_previsao_X.columns)

    columns, index_time_cols = get_indices_columns_time(df_previsao_X.columns)
    df_previsao_X = df_previsao_X[columns]

    # Precisa dessas variáveis para percorrer na previsão
    df_previsao_X['ano'] = [0] * df_previsao_X.shape[0]
    df_previsao_X['mes'] = [0] * df_previsao_X.shape[0]
    df_previsao_X['nome_bairro'] = [0] * df_previsao_X.shape[0]
    df_previsao_X['chave'] = [0] * df_previsao_X.shape[0]
    df_previsao_X['cod_bairro'] = [0] * df_previsao_X.shape[0]

    # Precisa dessas variáveis para percorrer na previsão
    df_previsao_X.loc[:,['ano']] = list(df_previsao['ano'])
    df_previsao_X.loc[:,['mes']] = list(df_previsao['mes'])
    df_previsao_X.loc[:,['nome_bairro']] = list(df_previsao['nome_bairro'])
    df_previsao_X.loc[:,['chave']] = list(df_previsao['chave'])
    df_previsao_X.loc[:,['cod_bairro']] = list(df_previsao['cod_bairro'])

    return df_previsao_X, columns


In [12]:
def network_neigboor(df, neighbor_columns):
    '''
    O método consolida as informações de vizinhança e casos
    :param path_input_read:
    :return: dataframe com colunas dos vizinhos de todos os bairros, cada posição de vizinhos tem
    a quantidade de casos de t-1, t-3 e t-6
    '''

    df_net = pd.read_excel(os.path.join(base_path, "data", "Pasta de trabalho.xlsx"),
                           sheet_name="Higienizado")
        # base_path + \
        # '/data_sus/input/Network_Bairros/Pasta de trabalho.xlsx',
        # sheet_name="Higienizado")

    columns_net = df['nome_bairro'].unique()

    df_net_geral = df.copy()

    # Cria a coluna de todas as regiões vizinhas
    for c in columns_net:
        df_net_geral[c + ' (t-1)'] = [np.nan] * df_net_geral.shape[0]
        if 'sum_vizinhos_t-3' in neighbor_columns:
            df_net_geral[c + ' (t-3)'] = [np.nan] * df_net_geral.shape[0]
        if 'sum_vizinhos_t-6' in neighbor_columns:
            df_net_geral[c + ' (t-6)'] = [np.nan] * df_net_geral.shape[0]

    df.index = df['nome_bairro']
    df_net_geral.index = df_net_geral['chave']

    # Cada linha do df_net possui a região na coluna Regiao e os respectivos vizinhos nas colunas seguintes
    for i in list(range(0, df_net.shape[0])):

        # connection é a linha que possui a região e os respectivos vizinhos
        connection = df_net.iloc[i, :]
        # c será a região de conexão, o range vai até 18 porque é o número máximo de vizinhos
        for c in list(range(1, 18)):

            # Se igual a zero significa que acabaram as regiões vizinhas e pode analisar ir para a próxima região
            if connection[c] == 0:
                break
            else:

                for a in list(df_net_geral['ano'].unique()):
                    for m in list(df_net_geral['mes'].unique()):
                        try:
                            aux = df[(df["ano"] == a) & (df["mes"] == m)]

                            # Para os casos em que nem todos os anos forem até 12 meses
                            if aux.shape[0] == 0:
                                continue

                            # Cria a chave para especificar a região, ano e mês que terá o valor inserido
                            # chave_regiao_origem = str(df_input.loc[connection['Regiao'], "cod_bairro"])\
                            #                       +str(a)+str(m)

                            chave_regiao_origem = str(aux.loc[connection['Regiao'], "cod_bairro"]) \
                                                  + str(a) + str(m)

                            # Busca a chave para a região de análise
                            # chave_regiao_conectada = str(df_input.loc[connection[c], "cod_bairro"])\
                            #                          +str(a)+str(m)
                            chave_regiao_conectada = str(aux.loc[connection[c], "cod_bairro"]) \
                                                     + str(a) + str(m)

                            # Na linha cidade conectada coloca os valores de t-1, soma até t-3 e soma até t-6
                            df_net_geral.loc[int(chave_regiao_origem), connection[c] + " (t-1)"] = np.sum(
                                df_net_geral.loc[
                                    int(chave_regiao_conectada), "t-1"])
                            if 'sum_vizinhos_t-3' in neighbor_columns:
                                df_net_geral.loc[int(chave_regiao_origem), connection[c] + " (t-3)"] = np.sum(
                                    df_net_geral.loc[
                                        int(chave_regiao_conectada), ["t-1", "t-2", "t-3"]])
                            if 'sum_vizinhos_t-6' in neighbor_columns:
                                df_net_geral.loc[int(chave_regiao_origem), connection[c] + " (t-6)"] = np.sum(
                                    df_net_geral.loc[
                                        int(chave_regiao_conectada), ["t-1", "t-2", "t-3", "t-4", "t-5", "t-6"]])
                        except Exception as ex:
                            print("error network neighbour")

    return df_net_geral

In [13]:
def sum_neighboors_to_prediction(df, neighbor_columns, taxa=False):
    '''
    Consolida as colunas de vizinhos nas colunas sum_vizinhos
    :param df_input:
    :return:
    '''
    if not taxa:

        df_input_net = network_neigboor(df, neighbor_columns)

        for c in list(df_input_net.columns):
            if re.match(".*Unname.*", c):
                df_input_net.drop(columns=[c], inplace=True)
            # elif c in ['min_vizinhos', 'max_vizinhos']:
            #     df_input.drop(columns=[c], inplace=True)

        columns_sequence, index_time_cols_um, index_time_cols_tres, index_time_cols_seis = \
            get_indices_columns_time2(list(df_input_net.columns))

        df_input_net = df_input_net[columns_sequence]

        sum_cases_um = list()
        sum_cases_tres = list()
        sum_cases_seis = list()

        for i in list(range(df_input_net.shape[0])):
            sum_cases_um.append(np.sum(df_input_net.iloc[i, index_time_cols_um[0]:index_time_cols_um[1]]))
            if 'sum_vizinhos_t-3' in neighbor_columns:
                sum_cases_tres.append(np.sum(df_input_net.iloc[i, index_time_cols_tres[0]:index_time_cols_tres[1]]))
            if 'sum_vizinhos_t-6' in neighbor_columns:
                sum_cases_seis.append(np.sum(df_input_net.iloc[i, index_time_cols_seis[0]:index_time_cols_seis[1]]))

        df['sum_vizinhos_t-1'] = sum_cases_um
        if 'sum_vizinhos_t-3' in neighbor_columns:
            df['sum_vizinhos_t-3'] = sum_cases_tres
        if 'sum_vizinhos_t-6' in neighbor_columns:
            df['sum_vizinhos_t-6'] = sum_cases_seis

        df['sum_vizinhos_t-1'] = df['sum_vizinhos_t-1'].apply(
            lambda x: round(x) if re.match(".*[0-9].*", str(x)) else 0)

        if 'sum_vizinhos_t-3' in neighbor_columns:
            df['sum_vizinhos_t-3'] = df['sum_vizinhos_t-3'].apply(
                lambda x: round(x) if re.match(".*[0-9].*", str(x)) else 0)

        if 'sum_vizinhos_t-6' in neighbor_columns:
            df['sum_vizinhos_t-6'] = df['sum_vizinhos_t-6'].apply(
                lambda x: round(x) if re.match(".*[0-9].*", str(x)) else 0)

    return df[neighbor_columns]


In [14]:
def apply_future_prediction_update_neighbors_v2(regressor, df_test, selected_columns,
                                             columns_filtered_categorical, train_columns,
                                             categorical_columns=[], neighbor_columns=[],
                                             target='dengue_diagnosis', scaler=False):
    '''
    d = list(df_previsao_X['date'].unique())[0]
    '''

    df_previsao_X, columns = prepare_base_test(df_test, selected_columns, columns_filtered_categorical,
                            categorical_columns, train_columns, scaler)
    df_previsao_X['date'] = df_previsao_X[['ano', 'mes']].apply(lambda x: date(x[0], x[1], 1), axis=1)

    list_results = list()
    df_result_consolidate = pd.DataFrame(
        columns=list(df_previsao_X.columns)+[target+"_previsto"])
    df_result_consolidate.drop(columns=['date'], inplace=True)

    for d in list(df_previsao_X['date'].unique()):
        # for num_pred in list(range(len(list(df_previsao_X['date'].unique())))):
            try:
                # Filtra o ano e mes que será previsto
                df_base = df_previsao_X[df_previsao_X['date'] == d]

                # Filtra mês em que a previsão vai começar
                df = df_previsao_X[df_previsao_X['date'] == list(df_previsao_X['date'].unique())[0]]
                df.drop(columns=['date'], inplace=True)

                # Se não for o primeiro, então precisa mover os casos para os
                # meses anteriores e recalcular os vizinhos
                if len(list_results) > 0:

                    # Atribui os valores que já foram previstos para o novo df
                    for n in list(range(1, len(list_results)+1)):
                        df['t-{}'.format(n)] = list_results[-n]

                    # Apaga as colunas dos vizinhos para calcular novamente
                    if not neighbor_columns == []:
                        for n in neighbor_columns:
                            df.drop(columns=[n], inplace=True)

                        # Ajustar soma casos dos vizinhos
                        df_neighbors = sum_neighboors_to_prediction(df.copy(), neighbor_columns)
                        for n in neighbor_columns:
                            df[n] = list(df_neighbors[n])

                df_prev = df.drop(columns=['nome_bairro', 'chave', 'ano', 'mes', 'cod_bairro'])
                df_prev = df_prev[columns]

                # Faz a previsão e armazena na lista de suporte e no df de resultado final
                list_results.append(regressor.predict(df_prev))
                if target == 'dengue_diagnosis':
                    list_results[-1] = [0 if a < 0 else round(a) for a in list_results[-1]]
                df_base[target+"_previsto"] = list_results[-1]
                df_result_consolidate = df_result_consolidate.append(df_base)

            except Exception as ex:
                print(ex)


    # Inverte novamente as colunas categóricas
    for cat in categorical_columns:
        for c in df_test[cat].unique():
            if cat + '_' + str(c) in list(df_result_consolidate.columns):
                df_result_consolidate.drop(columns=[cat + '_' + str(c)], inplace=True)

    df_result_consolidate.sort_values(by=["cod_bairro", "ano", "mes"], inplace=True)

    return df_result_consolidate

In [15]:
def build_model_prediction(months_ahead):
    '''
    Build dataframe, calculating predictions through diferents initial months
    :return:
    a = 2016
    initial_test_month = 1
    months_ahead = 3
    '''
    variables = ['nome_bairro', 'ano', 'mes_inicial', 'mes', target, target + '_previsto']
    variables.extend(selected_columns)
    df_consolidate = pd.DataFrame(columns=variables)

    for a in list_year:
        for initial_test_month in months:
            try:
                #este if existe pois os dados vão somente até 10/2020
                if (a == 2020 and initial_test_month > 12 - months_ahead) or (a == 2020 and initial_test_month in [10, 11, 12]):
                    break 
                    
                df_train, df_test, x_train, y_train = run_main_first_step_1(target,
                                                                               ano_teste=a,
                                                                               log=log_flag,
                                                                               mes_inicio_teste=initial_test_month,
                                                                               meses_previsao=months_ahead,
                                                                               dengue_columns=dengue_columns,
                                                                               columns_filtered=selected_columns,
                                                                               categorical_columns=categorical_columns,
                                                                               columns_filtered_categorical=columns_filtered_categorical,
                                                                               quartil=True)

                df_result, df_output_model, regressor = run_main_first_step_2(df_test, x_train, y_train,
                                                                              selected_columns,
                                                                              categorical_columns,
                                                                              columns_filtered_categorical,
                                                                              neighbor_columns, target, model,
                                                                              standart=standart)

                df_result['mes_inicial'] = [initial_test_month] * df_result.shape[0]

                df_consolidate = df_consolidate.append(
                    df_result[variables])

            except Exception as ex:
                print("error")

    return df_consolidate


In [16]:
def build_baseline_prediction(months_ahead):

    df_input = pd.read_csv(base_path + "/data/dengue_input_from_source_v10.csv")

    order = (2, 0, 0)
    seasonal_order = (1, 0, 0, 12)
    trend = 'n'

    hist_window = dateutil.relativedelta.relativedelta(months=48)
    time_prediction = dateutil.relativedelta.relativedelta(months=months_ahead)

    df_input['data'] = df_input['data'].apply(lambda x: date(int(str(x).split('-')[0]),
                                                             int(str(x).split('-')[1]),
                                                             int(str(x).split('-')[2])))

    columns = list(df_input.columns)
    columns.extend(['dengue_diagnosis_previsto'])
    columns.extend(['mes_inicial'])
    df_res_consolidate = pd.DataFrame(
        columns=columns)

    for b in list(df_input['nome_bairro'].unique()):
        for year in list_year:
            for initial_month in list(range(1, 13)):
                if year == 2020 and initial_month > 8:
                    continue
                try:
                    df = df_input[df_input['nome_bairro'] == b]

                    data_hist_begin = date(year, initial_month, 1) - hist_window

                    df_train = df[(df['data'] >= data_hist_begin) & (
                            df['data'] < date(year, initial_month, 1))]

                    df_test = df[(df['data'] >= date(year, initial_month, 1)) & \
                                 (df['data'] < date(year, initial_month, 1) + time_prediction)]
                    y_train = list(df_train[target])
                    model = SARIMAX(y_train, order=order, seasonal_order=seasonal_order,
                                    trend=trend, simple_differencing=True,
                                    enforce_invertibility=False, enforce_stationarity=False)
                    model_fit = model.fit(disp=False)
                    df_test['dengue_diagnosis_previsto'] = [
                        int(n) if n > 0 else 0 for n in model_fit.forecast(months_ahead)]
                    df_test['mes_inicial'] = [initial_month] * df_test.shape[0]
                    df_res_consolidate = df_res_consolidate.append(df_test)

                except Exception as ex:
                    print("error")

    return df_res_consolidate


In [17]:
def build_baseline_prediction(months_ahead):

    df_input = pd.read_csv(base_path + "/data/dengue_input_from_source_v10.csv")

    order = (2, 0, 0)
    seasonal_order = (1, 0, 0, 12)
    trend = 'n'

    hist_window = dateutil.relativedelta.relativedelta(months=48)
    time_prediction = dateutil.relativedelta.relativedelta(months=months_ahead)

    df_input['data'] = df_input['data'].apply(lambda x: date(int(str(x).split('-')[0]),
                                                             int(str(x).split('-')[1]),
                                                             int(str(x).split('-')[2])))

    columns = list(df_input.columns)
    columns.extend(['dengue_diagnosis_previsto'])
    columns.extend(['mes_inicial'])
    df_res_consolidate = pd.DataFrame(
        columns=columns)

    for b in list(df_input['nome_bairro'].unique()):
        for year in list_year:
            for initial_month in list(range(1, 13)):
                if year == 2020 and initial_month > 8:
                    continue
                try:
                    df = df_input[df_input['nome_bairro'] == b]

                    data_hist_begin = date(year, initial_month, 1) - hist_window

                    df_train = df[(df['data'] >= data_hist_begin) & (
                            df['data'] < date(year, initial_month, 1))]

                    df_test = df[(df['data'] >= date(year, initial_month, 1)) & \
                                 (df['data'] < date(year, initial_month, 1) + time_prediction)]
                    y_train = list(df_train[target])
                    model = SARIMAX(y_train, order=order, seasonal_order=seasonal_order,
                                    trend=trend, simple_differencing=True,
                                    enforce_invertibility=False, enforce_stationarity=False)
                    model_fit = model.fit(disp=False)
                    df_test['dengue_diagnosis_previsto'] = [
                        int(n) if n > 0 else 0 for n in model_fit.forecast(months_ahead)]
                    df_test['mes_inicial'] = [initial_month] * df_test.shape[0]
                    df_res_consolidate = df_res_consolidate.append(df_test)

                except Exception as ex:
                    print("error")

    return df_res_consolidate


In [18]:
def run_catboost(x_train, y_train, grid_search=False, standart=False):

    if standart:
        regressor = cb.CatBoostRegressor()

    else:
        regressor = cb.CatBoostRegressor(learning_rate=0.1,
                                         bootstrap_type='Bernoulli',
                                         grow_policy='Lossguide',
                                         boosting_type='Plain')

    regressor.fit(x_train, y_train)

    return regressor,0


In [65]:
a=list_year[0]
initial_test_month = months[0]
months_ahead = 1

df_train, df_test, x_train, y_train = run_main_first_step_1(target,
                                                                               ano_teste=a,
                                                                               log=log_flag,
                                                                               mes_inicio_teste=initial_test_month,
                                                                               meses_previsao=months_ahead,
                                                                               dengue_columns=dengue_columns,
                                                                               columns_filtered=selected_columns,
                                                                               categorical_columns=categorical_columns,
                                                                               columns_filtered_categorical=columns_filtered_categorical,
                                                                               quartil=True)




regressor = run_catboost(x_train, y_train)


0:	learn: 25.7453353	total: 4.29ms	remaining: 4.29s
1:	learn: 24.4099115	total: 8.4ms	remaining: 4.19s
2:	learn: 23.1042641	total: 12.6ms	remaining: 4.17s
3:	learn: 21.9549509	total: 16.4ms	remaining: 4.09s
4:	learn: 20.9092167	total: 20ms	remaining: 3.98s
5:	learn: 20.0946042	total: 24ms	remaining: 3.97s
6:	learn: 19.1278744	total: 28ms	remaining: 3.97s
7:	learn: 18.4286719	total: 32.7ms	remaining: 4.05s
8:	learn: 17.7876386	total: 36.9ms	remaining: 4.06s
9:	learn: 17.1175973	total: 40.4ms	remaining: 4s
10:	learn: 16.5523870	total: 43.9ms	remaining: 3.95s
11:	learn: 15.9841620	total: 47.5ms	remaining: 3.91s
12:	learn: 15.4201708	total: 51.4ms	remaining: 3.9s
13:	learn: 15.0006964	total: 55.7ms	remaining: 3.92s
14:	learn: 14.4807557	total: 59.8ms	remaining: 3.92s
15:	learn: 14.0087632	total: 63.4ms	remaining: 3.9s
16:	learn: 13.5482053	total: 67ms	remaining: 3.87s
17:	learn: 13.2048659	total: 71.2ms	remaining: 3.88s
18:	learn: 12.9546678	total: 75.4ms	remaining: 3.89s
19:	learn: 12.576

184:	learn: 4.5629195	total: 785ms	remaining: 3.46s
185:	learn: 4.5554108	total: 792ms	remaining: 3.46s
186:	learn: 4.5456147	total: 798ms	remaining: 3.47s
187:	learn: 4.5266303	total: 803ms	remaining: 3.47s
188:	learn: 4.5156457	total: 807ms	remaining: 3.46s
189:	learn: 4.5051875	total: 811ms	remaining: 3.46s
190:	learn: 4.5023398	total: 816ms	remaining: 3.46s
191:	learn: 4.4747060	total: 820ms	remaining: 3.45s
192:	learn: 4.4463468	total: 825ms	remaining: 3.45s
193:	learn: 4.4310704	total: 829ms	remaining: 3.45s
194:	learn: 4.4168716	total: 833ms	remaining: 3.44s
195:	learn: 4.3968720	total: 838ms	remaining: 3.44s
196:	learn: 4.3821062	total: 842ms	remaining: 3.43s
197:	learn: 4.3777052	total: 847ms	remaining: 3.43s
198:	learn: 4.3622570	total: 854ms	remaining: 3.44s
199:	learn: 4.3424516	total: 860ms	remaining: 3.44s
200:	learn: 4.3387639	total: 865ms	remaining: 3.44s
201:	learn: 4.3353880	total: 870ms	remaining: 3.44s
202:	learn: 4.3306270	total: 875ms	remaining: 3.43s
203:	learn: 

351:	learn: 3.1283498	total: 1.6s	remaining: 2.94s
352:	learn: 3.1228046	total: 1.6s	remaining: 2.94s
353:	learn: 3.1167318	total: 1.61s	remaining: 2.94s
354:	learn: 3.1112075	total: 1.61s	remaining: 2.94s
355:	learn: 3.1056007	total: 1.62s	remaining: 2.93s
356:	learn: 3.0984346	total: 1.62s	remaining: 2.92s
357:	learn: 3.0936701	total: 1.63s	remaining: 2.92s
358:	learn: 3.0880970	total: 1.63s	remaining: 2.92s
359:	learn: 3.0829575	total: 1.64s	remaining: 2.91s
360:	learn: 3.0795796	total: 1.64s	remaining: 2.9s
361:	learn: 3.0768940	total: 1.65s	remaining: 2.9s
362:	learn: 3.0736411	total: 1.65s	remaining: 2.9s
363:	learn: 3.0720327	total: 1.65s	remaining: 2.89s
364:	learn: 3.0701275	total: 1.66s	remaining: 2.88s
365:	learn: 3.0654794	total: 1.66s	remaining: 2.88s
366:	learn: 3.0617334	total: 1.67s	remaining: 2.88s
367:	learn: 3.0571716	total: 1.67s	remaining: 2.87s
368:	learn: 3.0509091	total: 1.68s	remaining: 2.87s
369:	learn: 3.0488672	total: 1.68s	remaining: 2.86s
370:	learn: 3.044

532:	learn: 2.4042322	total: 2.38s	remaining: 2.09s
533:	learn: 2.4003009	total: 2.39s	remaining: 2.08s
534:	learn: 2.3975768	total: 2.39s	remaining: 2.08s
535:	learn: 2.3949381	total: 2.4s	remaining: 2.08s
536:	learn: 2.3902246	total: 2.4s	remaining: 2.07s
537:	learn: 2.3885143	total: 2.41s	remaining: 2.07s
538:	learn: 2.3848448	total: 2.41s	remaining: 2.06s
539:	learn: 2.3822679	total: 2.42s	remaining: 2.06s
540:	learn: 2.3811157	total: 2.42s	remaining: 2.06s
541:	learn: 2.3787706	total: 2.43s	remaining: 2.05s
542:	learn: 2.3768179	total: 2.43s	remaining: 2.05s
543:	learn: 2.3741973	total: 2.44s	remaining: 2.04s
544:	learn: 2.3705263	total: 2.44s	remaining: 2.04s
545:	learn: 2.3683114	total: 2.44s	remaining: 2.03s
546:	learn: 2.3649260	total: 2.45s	remaining: 2.03s
547:	learn: 2.3591963	total: 2.45s	remaining: 2.02s
548:	learn: 2.3549599	total: 2.46s	remaining: 2.02s
549:	learn: 2.3508421	total: 2.46s	remaining: 2.01s
550:	learn: 2.3470052	total: 2.47s	remaining: 2.01s
551:	learn: 2.

712:	learn: 1.9753519	total: 3.16s	remaining: 1.27s
713:	learn: 1.9731219	total: 3.17s	remaining: 1.27s
714:	learn: 1.9712090	total: 3.17s	remaining: 1.26s
715:	learn: 1.9693017	total: 3.18s	remaining: 1.26s
716:	learn: 1.9671462	total: 3.18s	remaining: 1.26s
717:	learn: 1.9659795	total: 3.19s	remaining: 1.25s
718:	learn: 1.9639700	total: 3.19s	remaining: 1.25s
719:	learn: 1.9620997	total: 3.2s	remaining: 1.24s
720:	learn: 1.9607838	total: 3.2s	remaining: 1.24s
721:	learn: 1.9593678	total: 3.21s	remaining: 1.23s
722:	learn: 1.9578869	total: 3.21s	remaining: 1.23s
723:	learn: 1.9567598	total: 3.22s	remaining: 1.23s
724:	learn: 1.9550400	total: 3.22s	remaining: 1.22s
725:	learn: 1.9529868	total: 3.23s	remaining: 1.22s
726:	learn: 1.9508132	total: 3.23s	remaining: 1.21s
727:	learn: 1.9486714	total: 3.24s	remaining: 1.21s
728:	learn: 1.9470421	total: 3.24s	remaining: 1.2s
729:	learn: 1.9454874	total: 3.25s	remaining: 1.2s
730:	learn: 1.9446380	total: 3.25s	remaining: 1.2s
731:	learn: 1.942

...

276:	learn: 3.6140101	total: 1.19s	remaining: 3.1s
277:	learn: 3.6060013	total: 1.19s	remaining: 3.1s
278:	learn: 3.6003826	total: 1.2s	remaining: 3.1s
279:	learn: 3.5929324	total: 1.2s	remaining: 3.1s
280:	learn: 3.5898082	total: 1.21s	remaining: 3.09s
281:	learn: 3.5804041	total: 1.21s	remaining: 3.09s
282:	learn: 3.5711810	total: 1.22s	remaining: 3.08s
283:	learn: 3.5688498	total: 1.22s	remaining: 3.08s
284:	learn: 3.5644469	total: 1.23s	remaining: 3.08s
285:	learn: 3.5569285	total: 1.23s	remaining: 3.07s
286:	learn: 3.5546119	total: 1.23s	remaining: 3.07s
287:	learn: 3.5483798	total: 1.24s	remaining: 3.06s
288:	learn: 3.5402930	total: 1.24s	remaining: 3.06s
289:	learn: 3.5392170	total: 1.25s	remaining: 3.05s
290:	learn: 3.5241213	total: 1.25s	remaining: 3.05s
291:	learn: 3.5146107	total: 1.25s	remaining: 3.04s
292:	learn: 3.5031442	total: 1.26s	remaining: 3.04s
293:	learn: 3.4947489	total: 1.26s	remaining: 3.04s
294:	learn: 3.4854950	total: 1.27s	remaining: 3.03s
295:	learn: 3.4768

439:	learn: 2.7225804	total: 1.97s	remaining: 2.5s
440:	learn: 2.7204142	total: 1.97s	remaining: 2.5s
441:	learn: 2.7154381	total: 1.98s	remaining: 2.5s
442:	learn: 2.7116663	total: 1.98s	remaining: 2.5s
443:	learn: 2.7066597	total: 1.99s	remaining: 2.49s
444:	learn: 2.7036817	total: 1.99s	remaining: 2.49s
445:	learn: 2.6982842	total: 2s	remaining: 2.48s
446:	learn: 2.6960354	total: 2s	remaining: 2.48s
447:	learn: 2.6902320	total: 2.01s	remaining: 2.47s
448:	learn: 2.6881310	total: 2.01s	remaining: 2.47s
449:	learn: 2.6839365	total: 2.02s	remaining: 2.46s
450:	learn: 2.6786592	total: 2.02s	remaining: 2.46s
451:	learn: 2.6775546	total: 2.02s	remaining: 2.45s
452:	learn: 2.6751480	total: 2.03s	remaining: 2.45s
453:	learn: 2.6720856	total: 2.03s	remaining: 2.44s
454:	learn: 2.6709857	total: 2.04s	remaining: 2.44s
455:	learn: 2.6683694	total: 2.04s	remaining: 2.44s
456:	learn: 2.6649931	total: 2.04s	remaining: 2.43s
457:	learn: 2.6612714	total: 2.05s	remaining: 2.42s
458:	learn: 2.6599274	

615:	learn: 2.1882358	total: 2.74s	remaining: 1.71s
616:	learn: 2.1863575	total: 2.75s	remaining: 1.71s
617:	learn: 2.1840106	total: 2.76s	remaining: 1.7s
618:	learn: 2.1795377	total: 2.76s	remaining: 1.7s
619:	learn: 2.1761788	total: 2.77s	remaining: 1.69s
620:	learn: 2.1745381	total: 2.77s	remaining: 1.69s
621:	learn: 2.1711471	total: 2.77s	remaining: 1.69s
622:	learn: 2.1692691	total: 2.78s	remaining: 1.68s
623:	learn: 2.1673779	total: 2.78s	remaining: 1.68s
624:	learn: 2.1651711	total: 2.79s	remaining: 1.67s
625:	learn: 2.1634082	total: 2.79s	remaining: 1.67s
626:	learn: 2.1608537	total: 2.8s	remaining: 1.66s
627:	learn: 2.1586791	total: 2.8s	remaining: 1.66s
628:	learn: 2.1570096	total: 2.81s	remaining: 1.66s
629:	learn: 2.1552159	total: 2.81s	remaining: 1.65s
630:	learn: 2.1542370	total: 2.81s	remaining: 1.65s
631:	learn: 2.1513107	total: 2.82s	remaining: 1.64s
632:	learn: 2.1482901	total: 2.82s	remaining: 1.64s
633:	learn: 2.1464896	total: 2.83s	remaining: 1.63s
634:	learn: 2.14

791:	learn: 1.8432840	total: 3.52s	remaining: 924ms
792:	learn: 1.8418766	total: 3.52s	remaining: 920ms
793:	learn: 1.8408453	total: 3.53s	remaining: 916ms
794:	learn: 1.8397122	total: 3.53s	remaining: 911ms
795:	learn: 1.8385058	total: 3.54s	remaining: 907ms
796:	learn: 1.8364486	total: 3.54s	remaining: 903ms
797:	learn: 1.8358972	total: 3.55s	remaining: 898ms
798:	learn: 1.8335874	total: 3.55s	remaining: 894ms
799:	learn: 1.8314844	total: 3.56s	remaining: 889ms
800:	learn: 1.8299706	total: 3.56s	remaining: 885ms
801:	learn: 1.8285919	total: 3.56s	remaining: 880ms
802:	learn: 1.8278781	total: 3.57s	remaining: 876ms
803:	learn: 1.8268832	total: 3.57s	remaining: 871ms
804:	learn: 1.8245373	total: 3.58s	remaining: 867ms
805:	learn: 1.8235756	total: 3.58s	remaining: 862ms
806:	learn: 1.8211039	total: 3.59s	remaining: 858ms
807:	learn: 1.8193574	total: 3.59s	remaining: 853ms
808:	learn: 1.8177693	total: 3.59s	remaining: 849ms
809:	learn: 1.8167471	total: 3.6s	remaining: 844ms
810:	learn: 1

969:	learn: 1.5998469	total: 4.29s	remaining: 133ms
970:	learn: 1.5987446	total: 4.29s	remaining: 128ms
971:	learn: 1.5971840	total: 4.3s	remaining: 124ms
972:	learn: 1.5958315	total: 4.31s	remaining: 120ms
973:	learn: 1.5946280	total: 4.31s	remaining: 115ms
974:	learn: 1.5937089	total: 4.32s	remaining: 111ms
975:	learn: 1.5929021	total: 4.32s	remaining: 106ms
976:	learn: 1.5918155	total: 4.32s	remaining: 102ms
977:	learn: 1.5914932	total: 4.33s	remaining: 97.4ms
978:	learn: 1.5901173	total: 4.33s	remaining: 92.9ms
979:	learn: 1.5893556	total: 4.34s	remaining: 88.5ms
980:	learn: 1.5884057	total: 4.34s	remaining: 84.1ms
981:	learn: 1.5873153	total: 4.34s	remaining: 79.6ms
982:	learn: 1.5860173	total: 4.35s	remaining: 75.2ms
983:	learn: 1.5850725	total: 4.35s	remaining: 70.8ms
984:	learn: 1.5842354	total: 4.36s	remaining: 66.3ms
985:	learn: 1.5830649	total: 4.36s	remaining: 61.9ms
986:	learn: 1.5822585	total: 4.37s	remaining: 57.5ms
987:	learn: 1.5812253	total: 4.37s	remaining: 53.1ms
98

In [66]:

df_result, df_output_model, regressor = run_main_first_step_2(df_test, x_train, y_train,
                                                                              selected_columns,
                                                                              categorical_columns,
                                                                              columns_filtered_categorical,
                                                                              neighbor_columns, target, model,
                                                                              standart=standart);
#df_test = pd.merge(df_test, df_output_model[["chave", target+'_previsto']], on="chave", how="left")

0:	learn: 25.7453353	total: 6.14ms	remaining: 6.13s
1:	learn: 24.4099115	total: 11.3ms	remaining: 5.62s
2:	learn: 23.1042641	total: 18ms	remaining: 5.97s
3:	learn: 21.9549509	total: 22.3ms	remaining: 5.54s
4:	learn: 20.9092167	total: 27.2ms	remaining: 5.42s
5:	learn: 20.0946042	total: 31.6ms	remaining: 5.24s
6:	learn: 19.1278744	total: 36.1ms	remaining: 5.13s
7:	learn: 18.4286719	total: 40.1ms	remaining: 4.97s
8:	learn: 17.7876386	total: 44.2ms	remaining: 4.87s
9:	learn: 17.1175973	total: 47.9ms	remaining: 4.74s
10:	learn: 16.5523870	total: 51.4ms	remaining: 4.62s
11:	learn: 15.9841620	total: 55ms	remaining: 4.53s
12:	learn: 15.4201708	total: 59.5ms	remaining: 4.52s
13:	learn: 15.0006964	total: 63.9ms	remaining: 4.5s
14:	learn: 14.4807557	total: 67.9ms	remaining: 4.46s
15:	learn: 14.0087632	total: 71.6ms	remaining: 4.4s
16:	learn: 13.5482053	total: 75.1ms	remaining: 4.34s
17:	learn: 13.2048659	total: 79.2ms	remaining: 4.32s
18:	learn: 12.9546678	total: 83.6ms	remaining: 4.32s
19:	learn

182:	learn: 4.5758122	total: 785ms	remaining: 3.5s
183:	learn: 4.5672906	total: 791ms	remaining: 3.51s
184:	learn: 4.5629195	total: 797ms	remaining: 3.51s
185:	learn: 4.5554108	total: 801ms	remaining: 3.51s
186:	learn: 4.5456147	total: 807ms	remaining: 3.51s
187:	learn: 4.5266303	total: 811ms	remaining: 3.5s
188:	learn: 4.5156457	total: 816ms	remaining: 3.5s
189:	learn: 4.5051875	total: 820ms	remaining: 3.5s
190:	learn: 4.5023398	total: 825ms	remaining: 3.49s
191:	learn: 4.4747060	total: 828ms	remaining: 3.49s
192:	learn: 4.4463468	total: 833ms	remaining: 3.48s
193:	learn: 4.4310704	total: 837ms	remaining: 3.48s
194:	learn: 4.4168716	total: 841ms	remaining: 3.47s
195:	learn: 4.3968720	total: 845ms	remaining: 3.46s
196:	learn: 4.3821062	total: 849ms	remaining: 3.46s
197:	learn: 4.3777052	total: 853ms	remaining: 3.46s
198:	learn: 4.3622570	total: 858ms	remaining: 3.45s
199:	learn: 4.3424516	total: 862ms	remaining: 3.45s
200:	learn: 4.3387639	total: 866ms	remaining: 3.44s
201:	learn: 4.33

358:	learn: 3.0880970	total: 1.56s	remaining: 2.79s
359:	learn: 3.0829575	total: 1.57s	remaining: 2.79s
360:	learn: 3.0795796	total: 1.57s	remaining: 2.79s
361:	learn: 3.0768940	total: 1.58s	remaining: 2.78s
362:	learn: 3.0736411	total: 1.58s	remaining: 2.78s
363:	learn: 3.0720327	total: 1.59s	remaining: 2.77s
364:	learn: 3.0701275	total: 1.59s	remaining: 2.77s
365:	learn: 3.0654794	total: 1.6s	remaining: 2.77s
366:	learn: 3.0617334	total: 1.6s	remaining: 2.76s
367:	learn: 3.0571716	total: 1.61s	remaining: 2.76s
368:	learn: 3.0509091	total: 1.61s	remaining: 2.75s
369:	learn: 3.0488672	total: 1.61s	remaining: 2.75s
370:	learn: 3.0441036	total: 1.62s	remaining: 2.74s
371:	learn: 3.0362724	total: 1.62s	remaining: 2.74s
372:	learn: 3.0327720	total: 1.63s	remaining: 2.73s
373:	learn: 3.0285131	total: 1.63s	remaining: 2.73s
374:	learn: 3.0218508	total: 1.64s	remaining: 2.73s
375:	learn: 3.0183614	total: 1.64s	remaining: 2.72s
376:	learn: 3.0096953	total: 1.64s	remaining: 2.72s
377:	learn: 3.

536:	learn: 2.3902246	total: 2.34s	remaining: 2.02s
537:	learn: 2.3885143	total: 2.35s	remaining: 2.02s
538:	learn: 2.3848448	total: 2.35s	remaining: 2.01s
539:	learn: 2.3822679	total: 2.36s	remaining: 2.01s
540:	learn: 2.3811157	total: 2.37s	remaining: 2.01s
541:	learn: 2.3787706	total: 2.37s	remaining: 2s
542:	learn: 2.3768179	total: 2.37s	remaining: 2s
543:	learn: 2.3741973	total: 2.38s	remaining: 1.99s
544:	learn: 2.3705263	total: 2.38s	remaining: 1.99s
545:	learn: 2.3683114	total: 2.39s	remaining: 1.99s
546:	learn: 2.3649260	total: 2.39s	remaining: 1.98s
547:	learn: 2.3591963	total: 2.4s	remaining: 1.98s
548:	learn: 2.3549599	total: 2.4s	remaining: 1.97s
549:	learn: 2.3508421	total: 2.4s	remaining: 1.97s
550:	learn: 2.3470052	total: 2.41s	remaining: 1.96s
551:	learn: 2.3444719	total: 2.41s	remaining: 1.96s
552:	learn: 2.3417128	total: 2.42s	remaining: 1.95s
553:	learn: 2.3396166	total: 2.42s	remaining: 1.95s
554:	learn: 2.3366058	total: 2.43s	remaining: 1.95s
555:	learn: 2.3342994

718:	learn: 1.9639700	total: 3.12s	remaining: 1.22s
719:	learn: 1.9620997	total: 3.13s	remaining: 1.22s
720:	learn: 1.9607838	total: 3.14s	remaining: 1.21s
721:	learn: 1.9593678	total: 3.14s	remaining: 1.21s
722:	learn: 1.9578869	total: 3.15s	remaining: 1.2s
723:	learn: 1.9567598	total: 3.15s	remaining: 1.2s
724:	learn: 1.9550400	total: 3.15s	remaining: 1.2s
725:	learn: 1.9529868	total: 3.16s	remaining: 1.19s
726:	learn: 1.9508132	total: 3.16s	remaining: 1.19s
727:	learn: 1.9486714	total: 3.17s	remaining: 1.18s
728:	learn: 1.9470421	total: 3.17s	remaining: 1.18s
729:	learn: 1.9454874	total: 3.17s	remaining: 1.17s
730:	learn: 1.9446380	total: 3.18s	remaining: 1.17s
731:	learn: 1.9423823	total: 3.18s	remaining: 1.17s
732:	learn: 1.9395588	total: 3.19s	remaining: 1.16s
733:	learn: 1.9385701	total: 3.19s	remaining: 1.16s
734:	learn: 1.9371605	total: 3.2s	remaining: 1.15s
735:	learn: 1.9365488	total: 3.2s	remaining: 1.15s
736:	learn: 1.9351265	total: 3.2s	remaining: 1.14s
737:	learn: 1.9333

901:	learn: 1.6840779	total: 3.91s	remaining: 425ms
902:	learn: 1.6829971	total: 3.92s	remaining: 421ms
903:	learn: 1.6813772	total: 3.92s	remaining: 416ms
904:	learn: 1.6799329	total: 3.92s	remaining: 412ms
905:	learn: 1.6787208	total: 3.93s	remaining: 408ms
906:	learn: 1.6775797	total: 3.93s	remaining: 403ms
907:	learn: 1.6768361	total: 3.94s	remaining: 399ms
908:	learn: 1.6752052	total: 3.94s	remaining: 395ms
909:	learn: 1.6744066	total: 3.95s	remaining: 390ms
910:	learn: 1.6732445	total: 3.95s	remaining: 386ms
911:	learn: 1.6722975	total: 3.95s	remaining: 382ms
912:	learn: 1.6708834	total: 3.96s	remaining: 377ms
913:	learn: 1.6690154	total: 3.96s	remaining: 373ms
914:	learn: 1.6678198	total: 3.97s	remaining: 368ms
915:	learn: 1.6657958	total: 3.97s	remaining: 364ms
916:	learn: 1.6648974	total: 3.97s	remaining: 360ms
917:	learn: 1.6635229	total: 3.98s	remaining: 355ms
918:	learn: 1.6623530	total: 3.98s	remaining: 351ms
919:	learn: 1.6608471	total: 3.99s	remaining: 347ms
920:	learn: 

In [19]:
df_res = build_model_prediction(1)

0:	learn: 25.7453353	total: 64.4ms	remaining: 1m 4s
1:	learn: 24.4099115	total: 69.4ms	remaining: 34.6s
2:	learn: 23.1042641	total: 74.1ms	remaining: 24.6s
3:	learn: 21.9549509	total: 78.2ms	remaining: 19.5s
4:	learn: 20.9092167	total: 81.8ms	remaining: 16.3s
5:	learn: 20.0946042	total: 85.7ms	remaining: 14.2s
6:	learn: 19.1278744	total: 89.9ms	remaining: 12.8s
7:	learn: 18.4286719	total: 94ms	remaining: 11.7s
8:	learn: 17.7876386	total: 98ms	remaining: 10.8s
9:	learn: 17.1175973	total: 102ms	remaining: 10.1s
10:	learn: 16.5523870	total: 105ms	remaining: 9.46s
11:	learn: 15.9841620	total: 109ms	remaining: 8.95s
12:	learn: 15.4201708	total: 113ms	remaining: 8.55s
13:	learn: 15.0006964	total: 117ms	remaining: 8.23s
14:	learn: 14.4807557	total: 121ms	remaining: 7.94s
15:	learn: 14.0087632	total: 125ms	remaining: 7.66s
16:	learn: 13.5482053	total: 128ms	remaining: 7.41s
17:	learn: 13.2048659	total: 132ms	remaining: 7.21s
18:	learn: 12.9546678	total: 136ms	remaining: 7.04s
19:	learn: 12.576

187:	learn: 4.5266303	total: 846ms	remaining: 3.65s
188:	learn: 4.5156457	total: 852ms	remaining: 3.66s
189:	learn: 4.5051875	total: 858ms	remaining: 3.66s
190:	learn: 4.5023398	total: 862ms	remaining: 3.65s
191:	learn: 4.4747060	total: 867ms	remaining: 3.65s
192:	learn: 4.4463468	total: 871ms	remaining: 3.64s
193:	learn: 4.4310704	total: 875ms	remaining: 3.63s
194:	learn: 4.4168716	total: 879ms	remaining: 3.63s
195:	learn: 4.3968720	total: 883ms	remaining: 3.62s
196:	learn: 4.3821062	total: 888ms	remaining: 3.62s
197:	learn: 4.3777052	total: 892ms	remaining: 3.61s
198:	learn: 4.3622570	total: 896ms	remaining: 3.61s
199:	learn: 4.3424516	total: 901ms	remaining: 3.6s
200:	learn: 4.3387639	total: 905ms	remaining: 3.6s
201:	learn: 4.3353880	total: 909ms	remaining: 3.59s
202:	learn: 4.3306270	total: 913ms	remaining: 3.58s
203:	learn: 4.3266326	total: 917ms	remaining: 3.58s
204:	learn: 4.3227890	total: 921ms	remaining: 3.57s
205:	learn: 4.3149243	total: 925ms	remaining: 3.56s
206:	learn: 4.

361:	learn: 3.0768940	total: 1.64s	remaining: 2.89s
362:	learn: 3.0736411	total: 1.65s	remaining: 2.9s
363:	learn: 3.0720327	total: 1.66s	remaining: 2.89s
364:	learn: 3.0701275	total: 1.66s	remaining: 2.89s
365:	learn: 3.0654794	total: 1.67s	remaining: 2.88s
366:	learn: 3.0617334	total: 1.67s	remaining: 2.88s
367:	learn: 3.0571716	total: 1.67s	remaining: 2.87s
368:	learn: 3.0509091	total: 1.68s	remaining: 2.87s
369:	learn: 3.0488672	total: 1.68s	remaining: 2.86s
370:	learn: 3.0441036	total: 1.69s	remaining: 2.86s
371:	learn: 3.0362724	total: 1.69s	remaining: 2.85s
372:	learn: 3.0327720	total: 1.69s	remaining: 2.85s
373:	learn: 3.0285131	total: 1.7s	remaining: 2.84s
374:	learn: 3.0218508	total: 1.7s	remaining: 2.84s
375:	learn: 3.0183614	total: 1.71s	remaining: 2.83s
376:	learn: 3.0096953	total: 1.71s	remaining: 2.83s
377:	learn: 3.0051904	total: 1.71s	remaining: 2.82s
378:	learn: 3.0017374	total: 1.72s	remaining: 2.82s
379:	learn: 2.9987348	total: 1.72s	remaining: 2.81s
380:	learn: 2.9

538:	learn: 2.3848448	total: 2.42s	remaining: 2.07s
539:	learn: 2.3822679	total: 2.42s	remaining: 2.06s
540:	learn: 2.3811157	total: 2.43s	remaining: 2.06s
541:	learn: 2.3787706	total: 2.44s	remaining: 2.06s
542:	learn: 2.3768179	total: 2.44s	remaining: 2.05s
543:	learn: 2.3741973	total: 2.44s	remaining: 2.05s
544:	learn: 2.3705263	total: 2.45s	remaining: 2.04s
545:	learn: 2.3683114	total: 2.45s	remaining: 2.04s
546:	learn: 2.3649260	total: 2.46s	remaining: 2.03s
547:	learn: 2.3591963	total: 2.46s	remaining: 2.03s
548:	learn: 2.3549599	total: 2.46s	remaining: 2.02s
549:	learn: 2.3508421	total: 2.47s	remaining: 2.02s
550:	learn: 2.3470052	total: 2.47s	remaining: 2.02s
551:	learn: 2.3444719	total: 2.48s	remaining: 2.01s
552:	learn: 2.3417128	total: 2.48s	remaining: 2s
553:	learn: 2.3396166	total: 2.48s	remaining: 2s
554:	learn: 2.3366058	total: 2.49s	remaining: 2s
555:	learn: 2.3342994	total: 2.49s	remaining: 1.99s
556:	learn: 2.3314302	total: 2.5s	remaining: 1.99s
557:	learn: 2.3286557	

723:	learn: 1.9567598	total: 3.2s	remaining: 1.22s
724:	learn: 1.9550400	total: 3.21s	remaining: 1.22s
725:	learn: 1.9529868	total: 3.21s	remaining: 1.21s
726:	learn: 1.9508132	total: 3.22s	remaining: 1.21s
727:	learn: 1.9486714	total: 3.22s	remaining: 1.2s
728:	learn: 1.9470421	total: 3.23s	remaining: 1.2s
729:	learn: 1.9454874	total: 3.23s	remaining: 1.2s
730:	learn: 1.9446380	total: 3.23s	remaining: 1.19s
731:	learn: 1.9423823	total: 3.24s	remaining: 1.19s
732:	learn: 1.9395588	total: 3.24s	remaining: 1.18s
733:	learn: 1.9385701	total: 3.25s	remaining: 1.18s
734:	learn: 1.9371605	total: 3.25s	remaining: 1.17s
735:	learn: 1.9365488	total: 3.26s	remaining: 1.17s
736:	learn: 1.9351265	total: 3.26s	remaining: 1.16s
737:	learn: 1.9333901	total: 3.27s	remaining: 1.16s
738:	learn: 1.9315763	total: 3.27s	remaining: 1.15s
739:	learn: 1.9306461	total: 3.27s	remaining: 1.15s
740:	learn: 1.9285263	total: 3.28s	remaining: 1.15s
741:	learn: 1.9272144	total: 3.28s	remaining: 1.14s
742:	learn: 1.92

...

231:	learn: 4.0376982	total: 977ms	remaining: 3.23s
232:	learn: 4.0145445	total: 984ms	remaining: 3.24s
233:	learn: 3.9954753	total: 990ms	remaining: 3.24s
234:	learn: 3.9803852	total: 995ms	remaining: 3.24s
235:	learn: 3.9606038	total: 1000ms	remaining: 3.24s
236:	learn: 3.9528043	total: 1s	remaining: 3.23s
237:	learn: 3.9390938	total: 1.01s	remaining: 3.23s
238:	learn: 3.9304346	total: 1.01s	remaining: 3.23s
239:	learn: 3.9140140	total: 1.02s	remaining: 3.22s
240:	learn: 3.9049640	total: 1.02s	remaining: 3.22s
241:	learn: 3.8954599	total: 1.02s	remaining: 3.21s
242:	learn: 3.8893506	total: 1.03s	remaining: 3.21s
243:	learn: 3.8836954	total: 1.03s	remaining: 3.2s
244:	learn: 3.8680358	total: 1.04s	remaining: 3.2s
245:	learn: 3.8641559	total: 1.04s	remaining: 3.19s
246:	learn: 3.8624141	total: 1.05s	remaining: 3.19s
247:	learn: 3.8554816	total: 1.05s	remaining: 3.19s
248:	learn: 3.8410852	total: 1.05s	remaining: 3.18s
249:	learn: 3.8400787	total: 1.06s	remaining: 3.17s
250:	learn: 3.83

411:	learn: 2.8691221	total: 1.76s	remaining: 2.51s
412:	learn: 2.8651343	total: 1.76s	remaining: 2.51s
413:	learn: 2.8597141	total: 1.77s	remaining: 2.51s
414:	learn: 2.8559224	total: 1.78s	remaining: 2.5s
415:	learn: 2.8523961	total: 1.78s	remaining: 2.5s
416:	learn: 2.8484816	total: 1.79s	remaining: 2.5s
417:	learn: 2.8446832	total: 1.79s	remaining: 2.49s
418:	learn: 2.8414525	total: 1.79s	remaining: 2.49s
419:	learn: 2.8370966	total: 1.8s	remaining: 2.48s
420:	learn: 2.8345145	total: 1.8s	remaining: 2.48s
421:	learn: 2.8315788	total: 1.81s	remaining: 2.48s
422:	learn: 2.8267424	total: 1.81s	remaining: 2.47s
423:	learn: 2.8242144	total: 1.82s	remaining: 2.47s
424:	learn: 2.8200818	total: 1.82s	remaining: 2.46s
425:	learn: 2.8119236	total: 1.82s	remaining: 2.46s
426:	learn: 2.8095983	total: 1.83s	remaining: 2.45s
427:	learn: 2.8047743	total: 1.83s	remaining: 2.45s
428:	learn: 2.8025652	total: 1.84s	remaining: 2.44s
429:	learn: 2.7974891	total: 1.84s	remaining: 2.44s
430:	learn: 2.792

593:	learn: 2.3121858	total: 2.55s	remaining: 1.74s
594:	learn: 2.3081305	total: 2.55s	remaining: 1.74s
595:	learn: 2.3066066	total: 2.56s	remaining: 1.74s
596:	learn: 2.3040887	total: 2.57s	remaining: 1.73s
597:	learn: 2.3023422	total: 2.57s	remaining: 1.73s
598:	learn: 2.3019060	total: 2.57s	remaining: 1.72s
599:	learn: 2.3007528	total: 2.58s	remaining: 1.72s
600:	learn: 2.2983713	total: 2.58s	remaining: 1.72s
601:	learn: 2.2955644	total: 2.59s	remaining: 1.71s
602:	learn: 2.2929838	total: 2.59s	remaining: 1.71s
603:	learn: 2.2907605	total: 2.6s	remaining: 1.7s
604:	learn: 2.2889351	total: 2.6s	remaining: 1.7s
605:	learn: 2.2872704	total: 2.6s	remaining: 1.69s
606:	learn: 2.2837142	total: 2.61s	remaining: 1.69s
607:	learn: 2.2801507	total: 2.61s	remaining: 1.68s
608:	learn: 2.2784376	total: 2.62s	remaining: 1.68s
609:	learn: 2.2748736	total: 2.62s	remaining: 1.68s
610:	learn: 2.2724729	total: 2.63s	remaining: 1.67s
611:	learn: 2.2696123	total: 2.63s	remaining: 1.67s
612:	learn: 2.267

774:	learn: 1.9442962	total: 3.33s	remaining: 967ms
775:	learn: 1.9420991	total: 3.33s	remaining: 963ms
776:	learn: 1.9402904	total: 3.34s	remaining: 959ms
777:	learn: 1.9378941	total: 3.35s	remaining: 956ms
778:	learn: 1.9356611	total: 3.35s	remaining: 951ms
779:	learn: 1.9340492	total: 3.36s	remaining: 947ms
780:	learn: 1.9324505	total: 3.36s	remaining: 943ms
781:	learn: 1.9314184	total: 3.37s	remaining: 938ms
782:	learn: 1.9287984	total: 3.37s	remaining: 934ms
783:	learn: 1.9279713	total: 3.38s	remaining: 930ms
784:	learn: 1.9264693	total: 3.38s	remaining: 926ms
785:	learn: 1.9252628	total: 3.38s	remaining: 921ms
786:	learn: 1.9226733	total: 3.39s	remaining: 917ms
787:	learn: 1.9218833	total: 3.39s	remaining: 913ms
788:	learn: 1.9205766	total: 3.4s	remaining: 908ms
789:	learn: 1.9187928	total: 3.4s	remaining: 904ms
790:	learn: 1.9171516	total: 3.4s	remaining: 900ms
791:	learn: 1.9158709	total: 3.41s	remaining: 895ms
792:	learn: 1.9137434	total: 3.41s	remaining: 891ms
793:	learn: 1.9

955:	learn: 1.6902306	total: 4.11s	remaining: 189ms
956:	learn: 1.6889183	total: 4.11s	remaining: 185ms
957:	learn: 1.6869828	total: 4.12s	remaining: 181ms
958:	learn: 1.6839526	total: 4.13s	remaining: 176ms
959:	learn: 1.6826548	total: 4.14s	remaining: 172ms
960:	learn: 1.6808343	total: 4.14s	remaining: 168ms
961:	learn: 1.6792507	total: 4.15s	remaining: 164ms
962:	learn: 1.6780254	total: 4.16s	remaining: 160ms
963:	learn: 1.6765319	total: 4.16s	remaining: 155ms
964:	learn: 1.6751082	total: 4.17s	remaining: 151ms
965:	learn: 1.6741848	total: 4.17s	remaining: 147ms
966:	learn: 1.6728817	total: 4.17s	remaining: 142ms
967:	learn: 1.6712068	total: 4.18s	remaining: 138ms
968:	learn: 1.6705274	total: 4.18s	remaining: 134ms
969:	learn: 1.6693598	total: 4.19s	remaining: 129ms
970:	learn: 1.6684341	total: 4.19s	remaining: 125ms
971:	learn: 1.6675183	total: 4.19s	remaining: 121ms
972:	learn: 1.6668400	total: 4.2s	remaining: 117ms
973:	learn: 1.6645512	total: 4.2s	remaining: 112ms
974:	learn: 1.

In [68]:
variables = ['nome_bairro', 'ano', 'mes_inicial', 'mes', target, target + '_previsto']
variables.extend(selected_columns)
df_consolidate = pd.DataFrame(columns=variables)

df_result['mes_inicial'] = [initial_test_month] * df_result.shape[0]

df_consolidate = df_consolidate.append(df_result[variables])

In [69]:
df_consolidate.to_csv(base_path + f"/data/df_model_prediction_REPLICATION_YEAR.csv")


In [20]:
df_res.to_csv(base_path + f"/data/df_model_prediction_REPLICATION_YEAR.csv")